# Data exploration

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

# import missingno as msno 
## installing and importin the mapping library
!pip install folium
import folium

### Importing the data


In [ ]:
root_URL = 'https://raw.githubusercontent.com/StevenVuong/WDL_2020/master/data/stage1'

Churn_OD_file = 'Churn_OD.txt'
Churn_OD_URL = root_URL +'/'+ Churn_OD_file


County_Coordinates_Data_URL = 'https://raw.githubusercontent.com/Hardi-Lior/WDL/main/Stage_1/data/County_Coordinates_Data.csv'

In [ ]:
df_Churn_OD = pd.read_csv(Churn_OD_URL,delimiter="|",encoding = 'Latin1')
df_County_Coordinates_Data = pd.read_csv(County_Coordinates_Data_URL)

In [ ]:
df_Churn_OD.head()

Region_of_Origin  ... Demand_weight
0   R1 - AM Lisboa  ...      0.307323
1   R1 - AM Lisboa  ...      0.069997
2   R1 - AM Lisboa  ...      0.066059
3   R1 - AM Lisboa  ...      0.059847
4   R1 - AM Lisboa  ...      0.052341

[5 rows x 8 columns]

In [ ]:
df_Churn_OD.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2253 entries, 0 to 2252
Data columns (total 8 columns):
 #   Column                                       Non-Null Count  Dtype  
---  ------                                       --------------  -----  
 0   Region_of_Origin                             2253 non-null   object 
 1   District_of_Origin                           2253 non-null   object 
 2   County_of_Origin                             2253 non-null   object 
 3   Region_of_Public_Transportation              2253 non-null   object 
 4   District_of_Public_Transportation            2253 non-null   object 
 5   County_of_Public_Transportation              2253 non-null   object 
 6   Dicofre_ParishCode_of_Public_Transportation  2253 non-null   int64  
 7   Demand_weight                                2253 non-null   float64
dtypes: float64(1), int64(1), object(6)
memory usage: 140.9+ KB


In [ ]:
df_County_Coordinates_Data.head()

address  ...   County
0  amadora,lisboa,Portugal  ...  amadora
1  cascais,lisboa,Portugal  ...  cascais
2   lisboa,lisboa,Portugal  ...   lisboa
3   loures,lisboa,Portugal  ...   loures
4    mafra,lisboa,Portugal  ...    mafra

[5 rows x 7 columns]

# Mapping exersize
We are going to plot the the county that are listed in the Churn_OD file
1.   Adjust the Churn_OD to have more clean data format
2.   Get the coordinates for the county listed in Churn_OD file
3.   Mapping County on map visualisation 



*1.Adjust the Churn_OD to have more clean data format*

In [ ]:
# formating
df1['District_of_Origin'] = df1['District_of_Origin'].str.lower()
df1['County_of_Origin'] = df1['County_of_Origin'].str.lower()

df1['District_of_Public_Transportation'] = df1['District_of_Public_Transportation'].str.lower()
df1['County_of_Public_Transportation'] = df1['County_of_Public_Transportation'].str.lower()


df1.head()

Region_of_Origin  ... Demand_weight
0   R1 - AM Lisboa  ...      0.307323
1   R1 - AM Lisboa  ...      0.069997
2   R1 - AM Lisboa  ...      0.066059
3   R1 - AM Lisboa  ...      0.059847
4   R1 - AM Lisboa  ...      0.052341

[5 rows x 8 columns]

In [ ]:
# Creating sets of County to compare if all routes have a return route

set1 = set(df1['County_of_Origin'])
set2 = set(df1['County_of_Public_Transportation'])

set3 = set1.difference(set2)
set4 = set2.difference(set1)


We can see that set1 > set2, this mean that not all routes have return "path"

In [ ]:
print('size of set1:',len( set1))
print('size of set2:',len( set2))

size of set1: 34
size of set2: 18


 **set3** show the counties that don't have direct route back to

In [ ]:
for i in set3:
  print (i)

palmela
montijo
póvoa de varzim
espinho
cascais
santa maria da feira
são joão da madeira
alcochete
vila franca de xira
mafra
barreiro
oliveira de azeméis
moita
sesimbra
vale de cambra
setúbal


 **set4** show the counties that don't have direct route back to,
 but as **set4** is empty we assum that all counties in **set2** have return bus route???

In [ ]:
for i in set4:
  print (i)

I want to look for:

*   Number of bus journeys in the same Region and Region to Region 
*   Number of bus journeys from District to District
*   Number of bus journeys from County to County

In [ ]:
# i want to know the exact routes avalable
# df1["Region_Region"] = df1["Region_of_Origin"] + ' to ' + df1["Region_of_Public_Transportation"]
# df1["District_District"] = df1["District_of_Origin"] + ' to ' + df1["District_of_Public_Transportation"]
df1["County_County"] = df1["County_of_Origin"] + ' to ' + df1["County_of_Public_Transportation"]

In [ ]:
df_journeys = df1.drop_duplicates(subset=['County_County'])
df_journeys.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 442 entries, 0 to 2252
Data columns (total 9 columns):
 #   Column                                       Non-Null Count  Dtype  
---  ------                                       --------------  -----  
 0   Region_of_Origin                             442 non-null    object 
 1   District_of_Origin                           442 non-null    object 
 2   County_of_Origin                             442 non-null    object 
 3   Region_of_Public_Transportation              442 non-null    object 
 4   District_of_Public_Transportation            442 non-null    object 
 5   County_of_Public_Transportation              442 non-null    object 
 6   Dicofre_ParishCode_of_Public_Transportation  442 non-null    int64  
 7   Demand_weight                                442 non-null    float64
 8   County_County                                442 non-null    object 
dtypes: float64(1), int64(1), object(7)
memory usage: 34.5+ KB


In [ ]:
df_journeys = df_journeys.drop(columns=['County_County', 'Dicofre_ParishCode_of_Public_Transportation'])

In [ ]:
df_journeys.columns

Index(['Region_of_Origin', 'District_of_Origin', 'County_of_Origin',
       'Region_of_Public_Transportation', 'District_of_Public_Transportation',
       'County_of_Public_Transportation', 'Demand_weight'],
      dtype='object')

## 2.Get the coordinates for the county listed in Churn_OD file
 Accuaring County the coordinates 


In [ ]:
## we need the geopandas and geopy to get coordinates of the of the County in the data set 
## Geocoding service is built on top of OpenStreetMap data
!pip install geopandas
!pip install geopy

     |████████████████████████████████| 1.0MB 16.1MB/s 
     |████████████████████████████████| 6.5MB 38.3MB/s 
     |████████████████████████████████| 15.3MB 229kB/s 


In [ ]:
#Importing the Nominatim geocoder class 
from geopy.geocoders import Nominatim

## test code for getting the lovation data
# ## We create 'locator' that holds the Geocoding service, Nominatim will get us the coordinara from  the databas 
# locator = Nominatim(user_agent='myGeocoder')
# ## Then we pass the locator we created to geocode any address, in this example, the Eifel tower address.
# location = locator.geocode('Champ de Mars, Paris, France')
# print(location)
# print('Latitude = {}, Longitude = {}'.format(location.latitude, location.longitude))

In [ ]:
## creaeting datafram with proper formant to
df3 = pd.DataFrame()
location_points = pd.DataFrame()
df3['address'] = df1['County_of_Origin'] + ',' + df1['District_of_Origin'] + ',Portugal'

In [ ]:
#for val in df['address'].unique():
#  print (val)
location_points['address'] = df3['address'].unique()
location_points.head()

address
0  amadora,lisboa,Portugal
1  cascais,lisboa,Portugal
2   lisboa,lisboa,Portugal
3   loures,lisboa,Portugal
4    mafra,lisboa,Portugal

In [ ]:
from geopy.extra.rate_limiter import RateLimiter
## 1 - We create 'locator' that holds the Geocoding service, Nominatim will get us the coordinara from  the databas 
locator = Nominatim(user_agent='myGeocoder')
# 1 - conveneint function to delay between geocoding calls
geocode = RateLimiter(locator.geocode, min_delay_seconds=1)
# 2- - create location column
location_points['location'] = location_points['address'].apply(geocode)
# 3 - create longitude, laatitude and altitude from location column (returns tuple)
location_points['point'] = location_points['location'].apply(lambda loc: tuple(loc.point) if loc else None)

In [ ]:
# 4 - split point column into latitude, longitude and altitude columns
location_points[['latitude', 'longitude', 'altitude']] = pd.DataFrame(location_points['point'].tolist(), index=location_points.index)

In [ ]:
location_points.head()

address  ... altitude
0  amadora,lisboa,Portugal  ...      0.0
1  cascais,lisboa,Portugal  ...      0.0
2   lisboa,lisboa,Portugal  ...      0.0
3   loures,lisboa,Portugal  ...      0.0
4    mafra,lisboa,Portugal  ...      0.0

[5 rows x 6 columns]

In [ ]:
location_points['County'], location_points['AB'] = location_points['address'].str.split(',', 1).str
location_points = location_points.drop(['AB'], axis=1)
location_points.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  """Entry point for launching an IPython kernel.


address  ...   County
0  amadora,lisboa,Portugal  ...  amadora
1  cascais,lisboa,Portugal  ...  cascais
2   lisboa,lisboa,Portugal  ...   lisboa
3   loures,lisboa,Portugal  ...   loures
4    mafra,lisboa,Portugal  ...    mafra

[5 rows x 7 columns]

In [ ]:
County_lat_lon_df = pd.DataFrame()
County_lat_lon_df['County'] = location_points['County']
County_lat_lon_df['latitude'] = location_points['latitude']
County_lat_lon_df['longitude'] = location_points['longitude']
County_lat_lon_df.head()

County   latitude  longitude
0  amadora  38.759516  -9.223677
1  cascais  38.722400  -9.396909
2   lisboa  38.707751  -9.136592
3   loures  38.857864  -9.175816
4    mafra  38.936978  -9.328237

Format data 

In [ ]:
# convert to dic of counties and their coresponding coordinates
County_lat_lon_dict = County_lat_lon_df.set_index('County').T.to_dict('list')

In [ ]:
# we want to plot the 
df1_slim = df1.loc[:, df1.columns.intersection(['County_of_Origin', 'County_of_Public_Transportation','Demand_weight'])]
df1_slim.head()

County_of_Origin County_of_Public_Transportation  Demand_weight
0          amadora                          lisboa       0.307323
1          amadora                          lisboa       0.069997
2          amadora                          lisboa       0.066059
3          amadora                          lisboa       0.059847
4          amadora                          lisboa       0.052341

In [ ]:
df1_slim.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2253 entries, 0 to 2252
Data columns (total 3 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   County_of_Origin                 2253 non-null   object 
 1   County_of_Public_Transportation  2253 non-null   object 
 2   Demand_weight                    2253 non-null   float64
dtypes: float64(1), object(2)
memory usage: 52.9+ KB


In [ ]:
# getting that depature county coordinates and arrivel county coordinates
for idx, val in df1_slim['County_of_Origin'].iteritems():
    df1_slim.at[idx, 'dep_lat'], df1_slim.at[idx, 'dep_lon'] = County_lat_lon_dict[val]
for idx,val in df1_slim['County_of_Public_Transportation'].iteritems():
    df1_slim.at[idx, 'arr_lat'], df1_slim.at[idx, 'arr_lon'] = County_lat_lon_dict[val]
df1_slim.head()

County_of_Origin County_of_Public_Transportation  ...    arr_lat   arr_lon
0          amadora                          lisboa  ...  38.707751 -9.136592
1          amadora                          lisboa  ...  38.707751 -9.136592
2          amadora                          lisboa  ...  38.707751 -9.136592
3          amadora                          lisboa  ...  38.707751 -9.136592
4          amadora                          lisboa  ...  38.707751 -9.136592

[5 rows x 7 columns]

In [ ]:
# Sort by ascending county name
df1_slim = df1_slim.sort_values(by=['County_of_Origin'])
df1_slim.head()

County_of_Origin County_of_Public_Transportation  ...    arr_lat   arr_lon
732        alcochete                          lisboa  ...  38.707751 -9.136592
756        alcochete                          lisboa  ...  38.707751 -9.136592
755        alcochete                           porto  ...  41.149451 -8.610788
754        alcochete                           porto  ...  41.149451 -8.610788
753        alcochete                          lisboa  ...  38.707751 -9.136592

[5 rows x 7 columns]

## 3.Mapping County on map visualisation 

In [ ]:
!pip install folium


In [ ]:
import folium

map1 = folium.Map(
    location=[38.7223,-9.1393],
    tiles='cartodbpositron',
    zoom_start=11,
    min_zoom=4,
    max_zoom=14
)


path_coords = [[1,2],[3,4]]
location_points.apply(lambda row:folium.Marker(location=[row["latitude"], row["longitude"]],popup=row["address"] ).add_to(map1), axis=1)
count = 0
for val in range(len(df1_slim)):
  count = count + 1
  Feature_Group_Name = 'journy_from_' + str(df1_slim.County_of_Origin[val])
  Name = df1_slim.County_of_Origin[val]
  line = 'line_' + str(count)
  path_coords[0][0] = df1_slim.dep_lat[val]
  path_coords[0][1] = df1_slim.dep_lon[val]
  path_coords[1][0] = df1_slim.arr_lat[val]
  path_coords[1][1] = df1_slim.arr_lon[val]
  # Creating feature groups
  Name = folium.FeatureGroup(Feature_Group_Name)
  # Adding lines to the different feature groups
  line_1 =folium.vector_layers.PolyLine(path_coords,popup=Feature_Group_Name,tooltip=Feature_Group_Name,weight=5).add_to(Name)
  Name.add_to(map1)

folium.LayerControl().add_to(map1)


map1